# SEG/EAGE 3-D Salt Model

In this notebook we visualize the SEG/EAGE 3-D Salt Model from Aminzadeh et al., 1997. We use [PyVista](https://github.com/pyvista/pyvista) for the 3D visualization.

Much of the data IO for the salt model was adapted from [Dieter Werthmüller](https://github.com/prisae)'s work in [this example](https://nbviewer.jupyter.org/github/empymod/emg3d-examples/blob/master/2a_SEG-EAGE_3D-Salt-Model.ipynb) - thanks, Dieter!

Scroll down to see interactive renderings embedded in this notebook!

### Authors: 

- [Bane Sullivan](https://github.com/banesullivan): developer of [PyVista](https://github.com/pyvista/pyvista)
- [Dieter Werthmüller](https://github.com/prisae)

### References

- **Aminzadeh, F., Brac, J., and Kunz, T., 1997**, SEG/EAGE 3-D Salt and Overthrust Models, Society of Exploration Geophysicists, Tulsa, Oklahoma.

### Requirements

- `pyvista`, `pandas`, `joblib`, `panel`, `matplotlib`, `node.js`, `scooby`

## Download the data

You can get the data from the [SEG-website](https://wiki.seg.org/wiki/SEG/EAGE_Salt_and_Overthrust_Models) or via the [direct link](https://s3.amazonaws.com/open.source.geoscience/open_data/seg_eage_models_cd/Salt_Model_3D.tar.gz). The zip-file is 513.1 MB big. Unzip the archive and proceed.

### License information

The SEG/EAGE 3-D Salt and Overthrust Models (Aminzadeh et al., 1997) are released under the *Attribution 4.0 International* (**CC BY 4.0**) license. Consult the *README* and *LICENSE* files in the archive for more information.

In [1]:
import panel
import joblib
import pyvista as pv
import zipfile
import numpy as np
import pandas as pd
import glob
import os
import scooby

pv.rcParams['use_panel'] = True
panel.extension('vtk')

## Surfaces

Copy the `'Salt_Model_3D/3-D_Salt_Model/SURFACES/'` folder to the `'./data/'` directory in this repository

In [2]:
SURF_PATH = './data/SURFACES/'
if not os.path.isdir(SURF_PATH):
    raise RuntimeError('Yo! Place the `SURFACES` folder in the `data` directory.')
surface_files = glob.glob(os.path.join(SURF_PATH, '*.ts'))

faults = pv.MultiBlock()
layers = pv.MultiBlock()
horizons = pv.MultiBlock()
additional = pv.MultiBlock()

for file in surface_files:
    name = os.path.basename(file).replace('.ts', '').lower()
    table = pd.read_table(file, names=['type', 'a', 'b', 'c', 'd', 'e'], 
                          delim_whitespace=True)
    nodes = table[table['type'].str.contains('VRTX')][['b', 'c', 'd']].values
    # THE SEG/EAGE salt-model uses positive z downwards; so...
    # Flip the Z-coordinate reference
    nodes[:, -1] *= -1
    tris = table[table['type'] == 'TRGL'][['a', 'b', 'c']].values.astype(int) - 1
    faces = np.hstack(np.c_[np.full(len(tris), 3), tris])
    surf = pv.PolyData(nodes, faces)
    if name.startswith('fault'):
        faults[name] = surf
    elif name.startswith('layer'):
        layers[name] = surf
    elif name.startswith('hrz'):
        horizons[name] = surf
    else:
        additional[name] = surf
print('Done.')

Done.


## Salt Model

Copy the `'Salt_Model_3D/3-D_Salt_Model/VEL_GRIDS/'` folder to the `'./data/'` directory in this repository

In [3]:
DATAPATH = './data/VEL_GRIDS/'

# Dimensions
nx, ny, nz = 676, 676, 210

# Extract Saltf@@ from SALTF.ZIP
zipfile.ZipFile(DATAPATH+'SALTF.ZIP', 'r').extract('Saltf@@', path=DATAPATH)

# Load data
with open(DATAPATH+'Saltf@@', 'r') as file:
    vel = np.fromfile(file, dtype=np.dtype('float32').newbyteorder('>'))
    vel = vel.reshape(nx, ny, nz, order='F')
    
    # Cast type
    vel = np.asarray(vel, dtype=float)

    # THE SEG/EAGE salt-model uses positive z downwards;
    # here we want positive upwards. Hence:
    vel = np.flip(vel, 2)

# Create the PyVista UniformGrid
dimensions = (nx+1, ny+1, nz+1)
spacing = (20.,20.,20.)
origin = (0.,0.,-4200.)
mesh = pv.UniformGrid(dimensions, spacing, origin)

# Add data to the mesh
mesh['vel'] = vel.ravel('F')

mesh

UniformGrid (0x12f2d5dc8)
  N Cells:	95964960
  N Points:	96707419
  X Bounds:	0.000e+00, 1.352e+04
  Y Bounds:	0.000e+00, 1.352e+04
  Z Bounds:	-4.200e+03, 0.000e+00
  Dimensions:	677, 677, 211
  Spacing:	2.000e+01, 2.000e+01, 2.000e+01
  N Arrays:	1

# Visualize the Data

Let's first visualize the salt model along a few cross-sections and extract the salt body as a volumetric surface.

In [4]:
# Some display params to use for consistency
dparams = {'cmap': 'viridis', 'show_edges': False, 'clim': mesh.get_data_range()}
box = mesh.outline()

In [5]:
# Get three corss-sectional slices
slices = mesh.slice_orthogonal(x=5000, y=6000, z=-3200)
slices

MultiBlock (0x139ade588)
  N Blocks:	3
  X Bounds:	0.000, 13520.000
  Y Bounds:	0.000, 13520.000
  Z Bounds:	-4200.000, 0.000

In [6]:
# Extract the salt body by scalar values
# and decimate it's boundary with a 90% reduction target
# Why decimate it? it makes the rendering more easily shareable online
# Also, we smooth it over 50 iteration to make it a bit cleaner
rmin, rmax = 4480.0, 4484.0
salt_body = mesh.threshold([rmin, rmax]).decimate_boundary(0.90).smooth(50)
# Fill with scalar values on the surface
salt_body['vel'] = np.full(salt_body.n_cells, rmin)
salt_body

PolyData (0x139adeb28)
  N Cells:	66552
  N Points:	33238
  X Bounds:	3.640e+03, 1.162e+04
  Y Bounds:	2.860e+03, 1.046e+04
  Z Bounds:	-3.658e+03, -1.851e+02
  N Arrays:	1

In [9]:
# Display the data
p = pv.Plotter(notebook=False, title='foo')
p.add_mesh(slices, **dparams)
p.add_mesh(salt_body, **dparams)
# p.add_mesh(box, color='grey')
p.show_grid()
p.show()

TypeError: __init__() got an unexpected keyword argument 'title'

## Faults and the Salt Body

In [8]:
# Display the faults and the salt body
p = pv.Plotter()
p.add_mesh(faults, multi_colors=True)
p.add_mesh(salt_body, show_scalar_bar=False, **dparams)
p.add_mesh(box, color='grey')
p.show_grid()
p.show()

VTK(vtkCocoaRenderWindow, height=400, sizing_mode='stretch_width')

## Layers and the Salt Body

In [9]:
# Display the faults and the salt body
p = pv.Plotter()
p.add_mesh(layers, multi_colors=True)
p.add_mesh(salt_body, **dparams)
p.add_mesh(box, color='grey')
p.show_grid()
p.camera_position = [
 (-11386.44749303662, 7692.592539273874, -944.9898018895198),
 (6948.657622, 6852.7797304999995, -2100.0),
 (0.06324780761898185, 0.008332428153915016, 0.9979630681906281)]

p.show()

VTK(vtkCocoaRenderWindow, height=400, sizing_mode='stretch_width')

## Horizons and the Salt Body

In [10]:
# Display the faults and the salt body
p = pv.Plotter()
p.add_mesh(horizons, multi_colors=True)
p.add_mesh(salt_body, **dparams)
p.add_mesh(box, color='grey')
p.show_grid()
p.camera_position = [
 (7792.44319915045, -11355.158057849327, -1672.991043821196),
 (6859.3583515, 6829.069745, -1849.053612),
 (0.06336336258536848, 0.012913248834522977, 0.9979069757679885)]
p.show()

VTK(vtkCocoaRenderWindow, height=400, sizing_mode='stretch_width')

## Additional Surfaces and the Salt Body

In [ ]:
# Display the surface and the salt body
p = pv.Plotter(notebook=False)
p.add_mesh(additional, multi_colors=True)
p.add_mesh(salt_body, **dparams)
p.add_mesh(box, color='grey')
p.show_grid()
p.show()

In [11]:
pkgs = ['pyvista', 'pandas', 'joblib', 'panel', 'matplotlib', 'vtk']
scooby.Report(pkgs)

--------------------------------------------------------------------------------
  Date: Mon Jul 01 17:40:48 2019 MDT

            Darwin : OS
                12 : CPU(s)
            x86_64 : Machine
             64bit : Architecture
           32.0 GB : RAM
           Jupyter : Environment

  Python 3.7.3 | packaged by conda-forge | (default, Mar 27 2019, 15:43:19)
  [Clang 4.0.1 (tags/RELEASE_401/final)]

            0.21.0 : pyvista
            0.24.2 : pandas
            0.13.2 : joblib
           0.6.0a1 : panel
             3.1.0 : matplotlib
             8.2.0 : vtk
            1.16.3 : numpy
             1.3.0 : scipy
             7.5.0 : IPython
             0.4.0 : scooby

  Intel(R) Math Kernel Library Version 2018.0.3 Product Build 20180406 for
  Intel(R) 64 architecture applications
--------------------------------------------------------------------------------